# Data Cleaning

## Introduction

This notebook goes through the steps taken with the data collected in order to get cleaned organized data in two standard text formats. The notebook will contain the nexts steps.

1. **Cleaning the data -** I will use text pre-procesing techniques to get the dta into shape.
2. **Organizing the data -** I'l organize the data into a way that is easy to input into other algoithms

The output of this notebook will be clean, organized data in two standard text formats:

1. **Corpus** - a collection of texts
2. **Document-Term Matrix** - words counts in matrix format

### Problem Statement

My goal is to look look a the latest headlines of the main newspapers in Perú and note simmilarities and differences.

In [1]:
import emoji
import json
import numpy as np
import os
import pandas as pd
import plotly.express as px
import plotly.io as pio
import re
import string
import spacy

from collections import Counter
from dotenv import load_dotenv
from itertools import product
from num2words import num2words

Since most of the data we are dealing with is text data, I'm goig to be using some common text pre-processing techniques.

For that I'm going to follow the MVP __(Minimum Viable Product)__ approach. For that the main resource I'll be using is a talk from PyOhio by [Alice Zhao](https://github.com/adashofdata/nlp-in-python-tutorial/blob/master/1-Data-Cleaning.ipynb). The cleaning steps I'll be taking are.

**Removing tweets that are outside of the scope**

* Tweets corresponding to the cover page announcement
* Tweets corresponding to caricature of the day
* Tweets corresponding to the horoscope
* ...

**Common data cleaning steps on all text:**

* Make text all lowercase
* Remove punctuation
* Remove numerical values
* Remove common non.sensical text (\n)
* Tokenize text
* Remove stop words

**More data cleaning steps after tokenization:**

* Stemming/lemmatization
* Parts of speech tagging
* Create bi-grams or tri-grams
* Deal with typos

In [2]:
load_dotenv()

BASE_DIR = os.environ.get("BASE_DIR")
BEARER_TOKEN = os.environ.get("BEARER_TOKEN")

In [3]:
pd.set_option("display.max_colwidth", 300)
pd.set_option("display.max_rows", 25)
pd.set_option("display.precision", 2)
pd.set_option("display.float_format",  "{:,.2f}".format)

pio.templates.default = "plotly_white"
pio.kaleido.scope.default_scale = 2

gruvbox_colors = ["#458588", "#FABD2F", "#B8BB26", "#CC241D", "#B16286", "#8EC07C", "#FE8019"]

## Data Loading

In [4]:
TIME_STAMPS = [(2022, 35), (2022, 40), (2022, 45), (2022, 50), (2023, 3)]

In [5]:
with open(f'{BASE_DIR}/data/raw/newspapers_id.json', 'r') as read_file:
    newspapers_id = json.load(read_file)

In [6]:
newspaper_df_list = []

for newspaper, (year, week) in product(newspapers_id, TIME_STAMPS):

    with open(f'{BASE_DIR}/data/raw/{year}w{week}_data_{newspaper}.json', 'r') as read_file:
        json_file = json.load(read_file)

    json_data = json_file["data"]

    newspaper_df = pd.json_normalize(json_data)
    newspaper_df["newspaper"] = newspaper

    newspaper_df_list.append(newspaper_df)

In [7]:
data_raw = pd.concat(newspaper_df_list)

In [8]:
data_raw["created_at"] = pd.to_datetime(data_raw["created_at"], infer_datetime_format=True)

In [9]:
data_raw.columns = data_raw.columns.str.removeprefix("public_metrics.")

In [10]:
data_raw.head()

created_at  possibly_sensitive                   id  \
0 2022-08-28 23:57:24+00:00               False  1564039479391838209   
1 2022-08-28 23:49:59+00:00               False  1564037610393280512   
2 2022-08-28 23:29:00+00:00               False  1564032331706470401   
3 2022-08-28 23:14:11+00:00               False  1564028601053347843   
4 2022-08-28 23:09:07+00:00               False  1564027328157683713   

                                                                                                                                                 text  \
0                                                   Venezuela y Colombia retoman relaciones diplomáticas rotas hace tres años https://t.co/L6uVA6LcEE   
1  “Me dijeron que estaba llevando vergüenza a la universidad”: la profesora obligada a renunciar por postear fotos en bikini https://t.co/zAe98GI7W2   
2                                                         AMLO afirma que familias ya aceptaron plan de rescate de 10 mineros https://t.co/dG3VJXWgNa   
3                                              Zelensky: los ocupantes rusos sentirán las consecuencias de “futuras acciones” https://t.co/mNJTLz0SS7   
4                  Essalud: realizan con éxito operativo de donación de órganos para salvar vida de siete pacientes en espera https://t.co/3sDo7q9Nuu   

   retweet_count  reply_count  like_count  quote_count referenced_tweets  \
0              0            0           6            1               NaN   
1              0            0           5            1               NaN   
2              0            0           2            0               NaN   
3              6            7          18            1               NaN   
4              1            0          11            0               NaN   

         newspaper edit_history_tweet_ids  impression_count  
0  elcomercio_peru                    NaN               NaN  
1  elcomercio_peru                    NaN               NaN  
2  elcomercio_peru                    NaN               NaN  
3  elcomercio_peru                    NaN               NaN  
4  elcomercio_peru                    NaN               NaN

In [11]:
data_raw.tail()

created_at  possibly_sensitive                   id  \
19 2023-01-10 02:37:07+00:00               False  1612639646231527424   
20 2023-01-10 02:33:51+00:00               False  1612638821660721155   
21 2023-01-10 02:09:05+00:00               False  1612632590606794756   
22 2023-01-10 02:04:37+00:00               False  1612631466286133248   
23 2023-01-09 20:52:45+00:00               False  1612552984340078610   

                                                                                                                                                                                                                                                                                                           text  \
19                                        "Se va Tomás Unger, magnífico divulgador científico. Se jubila a los 92 años y lúcido. Yo nunca dejé de leerlo y le agradezco por todos estos años de información, de historias". #Hildebrandt ahora en su podcast de https://t.co/ofhuiX1sZu https://t.co/UrlOl4SUVd   
20  "@peru21noticias está quebrado, es un diario inviable. Entonces, Cecilia Valenzuela, Alfredo Torres y la hermana de Gilberto Hume están haciendo una bolsa para comprarlo. Necesitan un chaleco ilustrado de la derecha. Necesitan un diario combativo y doctrinario". #Hildebrandt https://t.co/7Xnmt3DAwO   
21                                                                                                "Señora Boluarte: si usted ha decidido no gobernar, renuncie. Usted espera, espera, espera, no sé qué espera y luego autoriza la bala". #Hildebrandt ahora en https://t.co/ofhuiX1sZu https://t.co/xamhBxUpTI   
22  "Los peruanos no escarmentamos, no aprendemos, siempre nos creemos por encima de todo. Van 40 muertos, señora @DinaErcilia. El gobierno no dialoga, no hace política y cuando la derecha le dice que está siendo pasivo, pide más muertos. El gobierno no dialoga, balea". #Hildebrandt https://t.co/4VU...   
23                                                        Hoy regresa el podcast de César #Hildebrandt. Va cada lunes a la 9 p.m. en https://t.co/ofhuiX1sZu. No se requiere suscripción ni pago alguno para ver la transmisión EN VIVO; para acceder al archivo de vídeos pasados, sí. https://t.co/VHjWhcGSY0   

    retweet_count  reply_count  like_count  quote_count referenced_tweets  \
19             25            9         226            3               NaN   
20            158           29         448           10               NaN   
21           1350          288        3774           46               NaN   
22           1036          310        2365           41               NaN   
23             95           34         438            3               NaN   

     newspaper edit_history_tweet_ids  impression_count  
19  ensustrece  [1612639646231527424]         16,189.00  
20  ensustrece  [1612638821660721155]         29,084.00  
21  ensustrece  [1612632590606794756]        159,409.00  
22  ensustrece  [1612631466286133248]         85,233.00  
23  ensustrece  [1612552984340078610]         29,116.00

In [12]:
data_raw.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 51235 entries, 0 to 23
Data columns (total 12 columns):
 #   Column                  Non-Null Count  Dtype              
---  ------                  --------------  -----              
 0   created_at              51235 non-null  datetime64[ns, UTC]
 1   possibly_sensitive      51235 non-null  bool               
 2   id                      51235 non-null  object             
 3   text                    51235 non-null  object             
 4   retweet_count           51235 non-null  int64              
 5   reply_count             51235 non-null  int64              
 6   like_count              51235 non-null  int64              
 7   quote_count             51235 non-null  int64              
 8   referenced_tweets       5091 non-null   object             
 9   newspaper               51235 non-null  object             
 10  edit_history_tweet_ids  34073 non-null  object             
 11  impression_count        7352 non-null   floa

In [13]:
data_raw["hour_posted"] = data_raw["created_at"].dt.time

In [14]:
data_raw.reset_index().to_feather(f"{BASE_DIR}/data/interim/data_raw-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.feather")

## First look on data

From the first looks, as well a the look on the head and tail I get to see how many of the variables are categorical and how many are numerical. Also, I only found missing values in the referenced tweets field. So, first for the numerical value I'm going to take a look of some metrics before the EDA.

**Numerical variables:**

1. `created_at`: Timestamp of the tweet
2. `retweet_count`: Number of times a tweet was retweeted
3. `like_count`: Number of likes a tweet has
4. `quote_count`: Number of times a tweet was quoted

**Categorical variables**

1. `id`: Unique identifier of tweet
2. `positively_sensitive`: Boolean variable of whether a tweet might contain sensitive information
3. `text`: Actual text of the tweet
4. `referenced_tweet`: Whether this tweet is a retweet or a quoted tweet
5. `newspaper`: Twitter handle if the newspaper the tweet belongs to

In [15]:
fig = px.histogram(
    data_raw,
    x="created_at",
    color_discrete_sequence=gruvbox_colors,
    facet_row="newspaper",
    title="Number of tweets per newspaper",
    height=1600,
    width=1000
)

fig.update_traces(xbins_size="D1")
fig.for_each_annotation(lambda a: a.update(text=f"@{a.text.split('=')[-1]}"))

fig.show()

# fig.write_image(f"{BASE_DIR}/reports/figures/1-histogram-tweeets-per-newspaper-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.jpg")

In [16]:
fig = px.scatter(
    data_raw,
    x="created_at",
    y="hour_posted",
    color_discrete_sequence=gruvbox_colors,
    facet_row="newspaper",
    title="Number of tweets per newspaper",
    height=1600,
    width=1000
)

# fig.update_traces(xbins_size="D1")
fig.for_each_annotation(lambda a: a.update(text=f"@{a.text.split('=')[-1]}"))
fig.update_traces(marker_size=2)

fig.show()

# fig.write_image(f"{BASE_DIR}/reports/figures/1-scatter-tweeets-per-newspaper-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.jpg")

In [17]:
data_stats = pd.DataFrame()

data_stats["raw_tweet_count"] = data_raw["newspaper"].value_counts()

data_stats = data_stats.merge(data_raw.loc[data_raw["referenced_tweets"].notna(), "newspaper"].value_counts(), how="left", left_index=True, right_index=True)
data_stats.rename(columns={"newspaper": "raw_referenced_tweet_count"}, inplace=True)

data_stats = data_stats.merge(data_raw.loc[data_raw["possibly_sensitive"] == True, "newspaper"].value_counts(), how="left", left_index=True, right_index=True)
data_stats.rename(columns={"newspaper": "raw_possibly_sensitive_count"}, inplace=True)

data_stats = data_stats.merge(data_raw.groupby("newspaper").sum(numeric_only=True).drop("possibly_sensitive", axis=1), how="left", left_index=True, right_index=True)
data_stats.rename(columns={"retweet_count": "raw_retweet_count", "reply_count": "raw_reply_count", "like_count": "raw_like_count", "quote_count": "raw_quote_count"}, inplace=True)

In [18]:
data_raw[data_raw["possibly_sensitive"] == True]

created_at  possibly_sensitive                   id  \
108 2022-10-02 03:09:17+00:00                True  1576408955529707521   
98  2022-11-05 19:01:18+00:00                True  1588969725387751430   
114 2023-01-14 18:34:06+00:00                True  1614330031181905926   
439 2022-11-04 17:41:08+00:00                True  1588587161699352577   
100 2023-01-14 20:02:19+00:00                True  1614352230651465731   
426 2022-09-30 18:31:32+00:00                True  1575916269525778442   
742 2022-12-05 21:35:28+00:00                True  1599880158810365977   
249 2022-11-04 17:16:09+00:00                True  1588580874186104832   
71  2022-12-11 14:05:39+00:00                True  1601941285023129602   
111 2023-01-11 19:57:50+00:00                True  1613263940049330176   

                                                                                                                                                                                                       text  \
108                                                                                                                 Bebé recién nacido fue encontrado en la basura al sur de Bogotá https://t.co/WJCnELvkR0   
98                                                                                             Campaña de vasectomía gratuita: ¿la ligadura de trompas está disponible todo el año? https://t.co/LImvmUT2JE   
114                                                                                                                    Miraflores: lobo marino queda varado en playa Punta Roquitas https://t.co/PuQnEIQZw7   
439                                                                            Vasectomía gratis del 14 al 18 de noviembre en hospitales de Lima: ¿Cómo se realiza la intervención? https://t.co/3Bc9h9e20O   
100                                                                                                 ¡Necesita ayuda! Lobo marino quedó varado en playa Punta Roquitas de Miraflores https://t.co/mJQv2XsPGB   
426                                                                             Yahaira Plasencia sufrió incidente en Iquitos: le jalonearon el cabello antes de subir al escenario https://t.co/k1rbS4PGwr   
742                                                                                    Aumentan a 40 las niñas entre 11 a 14 años que ya se convirtieron en madres en la región Ica https://t.co/cP9HBb7Bkd   
249                                                        Vasectomía gratis del 14 al 18 de noviembre en Lima: ¿afecta el deseo sexual? todo sobre este procedimiento para varones https://t.co/DQ9x0n7HBe   
71                                                                                                                       Comer para vivir: Cómo reducir la preferencia por lo dulce https://t.co/4ru7CmiKhR   
111  #Juliaca | Recogen restos de bombas lacrimógenas y munición que usó la policía contra manifestantes en el lugar donde  recibieron los féretros de los fallecidos en protestas. https://t.co/sBEPFGD5ss   

     retweet_count  reply_count  like_count  quote_count referenced_tweets  \
108              4            1          12            0               NaN   
98               0            1           1            0               NaN   
114              1            1           3            1               NaN   
439              6            1           2            2               NaN   
100              3            0          12            0               NaN   
426              1            0           3            0               NaN   
742              1            5           4            0               NaN   
249              1            0           2            0               NaN   
71               0            0           2            0               NaN   
111             22            3          33            0               NaN   

           newspaper edit_history_tweet_ids  impression_count hour_

In [17]:
data_stats["raw_reference_to_tweets_ratio"] = data_stats["raw_referenced_tweet_count"]/data_stats["raw_tweet_count"]
data_stats["raw_sensitive_to_tweets_ratio"] = data_stats["raw_possibly_sensitive_count"]/data_stats["raw_tweet_count"]
data_stats["raw_retweet_to_tweets_ratio"] = data_stats["raw_retweet_count"]/data_stats["raw_tweet_count"]
data_stats["raw_reply_to_tweets_ratio"] = data_stats["raw_reply_count"]/data_stats["raw_tweet_count"]
data_stats["raw_like_to_tweets_ratio"] = data_stats["raw_like_count"]/data_stats["raw_tweet_count"]
data_stats["raw_quote_to_tweets_ratio"] = data_stats["raw_quote_count"]/data_stats["raw_tweet_count"]

I decided to look at ratios related to the total ammount of tweets, because, as seen from the graph above, there is a big difference in the ammount of tweets from each newspaper.

In [18]:
data_stats.T

Gestionpe  peru21noticias      tromepe  \
raw_tweet_count                   8,169.00        7,571.00     7,186.00   
raw_referenced_tweet_count           30.00          244.00         3.00   
raw_possibly_sensitive_count           NaN            2.00         1.00   
raw_retweet_count                11,985.00       61,410.00     8,924.00   
raw_reply_count                  11,074.00       45,983.00    19,886.00   
raw_like_count                   46,076.00      197,619.00    56,303.00   
raw_quote_count                   1,717.00        6,378.00     1,537.00   
impression_count              3,312,134.00    3,880,890.00 1,606,484.00   
raw_reference_to_tweets_ratio         0.00            0.03         0.00   
raw_sensitive_to_tweets_ratio          NaN            0.00         0.00   
raw_retweet_to_tweets_ratio           1.47            8.11         1.24   
raw_reply_to_tweets_ratio             1.36            6.07         2.77   
raw_like_to_tweets_ratio              5.64           26.10         7.84   
raw_quote_to_tweets_ratio             0.21            0.84         0.21   

                               larepublica_pe  diarioojo  diariocorreo  \
raw_tweet_count                      7,064.00   5,063.00      4,841.00   
raw_referenced_tweet_count           4,065.00        NaN          4.00   
raw_possibly_sensitive_count              NaN       2.00          1.00   
raw_retweet_count                  137,796.00   2,800.00     15,481.00   
raw_reply_count                     28,637.00   7,616.00     14,963.00   
raw_like_count                     142,432.00  20,775.00     47,437.00   
raw_quote_count                      5,968.00     624.00      1,983.00   
impression_count                 5,505,507.00 405,654.00  1,201,940.00   
raw_reference_to_tweets_ratio            0.58        NaN          0.00   
raw_sensitive_to_tweets_ratio             NaN       0.00          0.00   
raw_retweet_to_tweets_ratio             19.51       0.55          3.20   
raw_reply_to_tweets_ratio                4.05       1.50          3.09   
raw_like_to_tweets_ratio                20.16       4.10          9.80   
raw_quote_to_tweets_ratio                0.84       0.12          0.41   

                               elcomercio_peru  ExpresoPeru  DiarioElPeruano  \
raw_tweet_count                       4,529.00     2,599.00         2,305.00   
raw_referenced_tweet_count              258.00          NaN            68.00   
raw_possibly_sensitive_count              3.00          NaN              NaN   
raw_retweet_count                    18,388.00    90,404.00        12,838.00   
raw_reply_count                      10,625.00    82,260.00        10,078.00   
raw_like_count                       40,572.00   299,029.00        34,004.00   
raw_quote_count                       1,616.00     9,158.00         1,135.00   
impression_count                  2,661,255.00 3,780,412.00     1,696,783.00   
raw_reference_to_tweets_ratio             0.06          NaN             0.03   
raw_sensitive_to_tweets_ratio             0.00          NaN              NaN   
raw_retweet_to_tweets_ratio               4.06        34.78             5.57   
raw_reply_to_tweets_ratio                 2.35        31.65             4.37   
raw_like_to_tweets_ratio                  8.96       115.06            14.75   
raw_quote_to_tweets_ratio                 0.36         3.52             0.49   

                               elbuho_pe  larazon_pe  ensustrece  
raw_tweet_count                   899.00      879.00      130.00  
raw_referenced_tweet_count        395.00         NaN       24.00  
raw_possibly_sensitive_count        1.00         NaN         NaN  
raw_retweet_count              11,472.00    2,477.00   21,269.00  
raw_reply_count                   828.00      458.00    5,180.00  
raw_like_count                  9,241.00    4,666.00   44,677.00  
raw_quote_count                   346.00      131.00      918.00  
impression_count              406,532.00   39,958.00  761,7

In [19]:
data_stats.to_csv(f"{BASE_DIR}/reports/tables/1-raw_stats-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.csv")

## Removing non relevant tweets

From checking the tweet feeds, and dataframe, I noticed that there are tweets that do not speak of the discourse of the newspaper, such as horoscopes caricatures and portada post.

In [17]:
data = data_raw

data.drop(data[data["text"].str.contains('horóscopo diario', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('horóscopo de', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('horóscopo hoy', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('horóscopo y tarot', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('horóscopo', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('Buenos días', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('caricatura de', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('las caricaturas de', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('portada impresa', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('portada de hoy', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('en portada', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('trome gol', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('no te pierdas las chiquitas de hoy', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data[data["text"].str.contains('esta es la portada', flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data.loc[data["text"].str.contains("Aquí la portada del", flags=re.IGNORECASE, regex=True)].index, inplace=True)
data.drop(data.loc[data["text"].str.contains("yapaza", flags=re.IGNORECASE, regex=True)].index, inplace=True)

In [21]:
data_stats = data_stats.merge(data["newspaper"].value_counts(), how="left", left_index=True, right_index=True)
data_stats.rename(columns={"newspaper": "clean_tweet_count"}, inplace=True)

data_stats = data_stats.merge(data.loc[data["referenced_tweets"].notna(), "newspaper"].value_counts(), how="left", left_index=True, right_index=True)
data_stats.rename(columns={"newspaper": "clean_referenced_tweet_count"}, inplace=True)

data_stats = data_stats.merge(data.loc[data["possibly_sensitive"] == True, "newspaper"].value_counts(), how="left", left_index=True, right_index=True)
data_stats.rename(columns={"newspaper": "clean_possibly_sensitive_count"}, inplace=True)

data_stats = data_stats.merge(data.groupby("newspaper").sum(numeric_only=True).drop("possibly_sensitive", axis=1), how="left", left_index=True, right_index=True)
data_stats.rename(columns={"retweet_count": "clean_retweet_count", "reply_count": "clean_reply_count", "like_count": "clean_like_count", "quote_count": "clean_quote_count"}, inplace=True)

In [22]:
data_stats.rename(columns={"impression_count_x": "raw_impression_count", "impression_count_y": "clean_impression_count"}, inplace=True)

In [23]:
data_stats["clean_to_raw_tweet_ratio"] = data_stats["clean_tweet_count"]/data_stats["raw_tweet_count"]
data_stats["clean_to_raw_impression_ratio"] = data_stats["clean_impression_count"]/data_stats["raw_impression_count"]

In [24]:
data_stats["clean_reference_to_tweets_ratio"] = data_stats["clean_referenced_tweet_count"]/data_stats["clean_tweet_count"]
data_stats["clean_sensitive_to_tweets_ratio"] = data_stats["clean_possibly_sensitive_count"]/data_stats["clean_tweet_count"]
data_stats["clean_retweet_to_tweets_ratio"] = data_stats["clean_retweet_count"]/data_stats["clean_tweet_count"]
data_stats["clean_reply_to_tweets_ratio"] = data_stats["clean_reply_count"]/data_stats["clean_tweet_count"]
data_stats["clean_like_to_tweets_ratio"] = data_stats["clean_like_count"]/data_stats["clean_tweet_count"]
data_stats["clean_quote_to_tweets_ratio"] = data_stats["clean_quote_count"]/data_stats["clean_tweet_count"]

In [25]:
data_stats = data_stats.T

In [26]:
data_stats

Gestionpe  peru21noticias   tromepe  \
raw_tweet_count                   8,169.00        7,571.00  7,186.00   
raw_referenced_tweet_count           30.00          244.00      3.00   
raw_possibly_sensitive_count           NaN            2.00      1.00   
raw_retweet_count                11,985.00       61,410.00  8,924.00   
raw_reply_count                  11,074.00       45,983.00 19,886.00   
...                                    ...             ...       ...   
clean_sensitive_to_tweets_ratio        NaN             NaN       NaN   
clean_retweet_to_tweets_ratio         1.44            7.70      1.15   
clean_reply_to_tweets_ratio           1.34            5.60      2.34   
clean_like_to_tweets_ratio            5.47           24.54      6.93   
clean_quote_to_tweets_ratio           0.21            0.84      0.21   

                                 larepublica_pe  diarioojo  diariocorreo  \
raw_tweet_count                        7,064.00   5,063.00      4,841.00   
raw_referenced_tweet_count             4,065.00        NaN          4.00   
raw_possibly_sensitive_count                NaN       2.00          1.00   
raw_retweet_count                    137,796.00   2,800.00     15,481.00   
raw_reply_count                       28,637.00   7,616.00     14,963.00   
...                                         ...        ...           ...   
clean_sensitive_to_tweets_ratio             NaN       0.00          0.00   
clean_retweet_to_tweets_ratio             19.41       0.51          3.00   
clean_reply_to_tweets_ratio                3.58       1.57          2.96   
clean_like_to_tweets_ratio                18.16       4.08          9.22   
clean_quote_to_tweets_ratio                0.74       0.13          0.41   

                                 elcomercio_peru  ExpresoPeru  \
raw_tweet_count                         4,529.00     2,599.00   
raw_referenced_tweet_count                258.00          NaN   
raw_possibly_sensitive_count                3.00          NaN   
raw_retweet_count                      18,388.00    90,404.00   
raw_reply_count                        10,625.00    82,260.00   
...                                          ...          ...   
clean_sensitive_to_tweets_ratio             0.00          NaN   
clean_retweet_to_tweets_ratio               3.92        30.58   
clean_reply_to_tweets_ratio                 2.00        30.46   
clean_like_to_tweets_ratio                  8.24       101.75   
clean_quote_to_tweets_ratio                 0.36         3.28   

                                 DiarioElPeruano  elbuho_pe  larazon_pe  \
raw_tweet_count                         2,305.00     899.00      879.00   
raw_referenced_tweet_count                 68.00     395.00         NaN   
raw_possibly_sensitive_count                 NaN       1.00         NaN   
raw_retweet_count                      12,838.00  11,472.00    2,477.00   
raw_reply_count                        10,078.00     828.00      458.00   
...                                          ...        ...         ...   
clean_sensitive_to_tweets_ratio              NaN        NaN         NaN   
clean_retweet_to_tweets_ratio               5.62      10.42        0.70   
clean_reply_to_tweets_ratio                 4.80       0.78        0.15   
clean_like_to_tweets_ratio                 16.07       6.13        1.47   
clean_quote_to_tweets_ratio                 0.48       0.23        0.07   

                                 ensustrece  
raw_tweet_count                      130.00  
raw_referenced_tweet_count            24.00  
raw_possibly_sensitive_count            NaN  
raw_retweet_count                 21,269.00  
raw_reply_count                    5,180.00  
...                                     ...  
clean_sensitive_to_tweets_ratio         NaN  
clean_retweet_to_tweets_ratio        122.25  
clean_reply_to_tweets_ratio           29.60  
clean_like_to_tweets_ratio           277.91  
clean_quote_to_tweets_ratio            5.30  

[30 rows x 12 column

In [27]:
data_stats.to_csv(f"{BASE_DIR}/reports/tables/1-clean_stats-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.csv")

## Extracting @mentions and #hashtags

In [18]:
data["mentions"] = data["text"].apply(lambda x: re.findall("@(\w+)", x))
data["hasthags"] = data["text"].apply(lambda x: re.findall("#(\w+)", x))

In [19]:
data.sample(10)

created_at  possibly_sensitive                   id  \
353  2023-01-10 18:16:51+00:00               False  1612876136089899009   
183  2022-09-27 03:43:47+00:00               False  1574605695340597248   
324  2022-09-29 22:58:43+00:00               False  1575621121596182531   
92   2022-08-28 14:54:13+00:00               False  1563902779206287361   
683  2022-12-06 20:11:02+00:00               False  1600221298151591976   
655  2023-01-10 17:34:43+00:00               False  1612865534684532760   
1143 2022-12-06 18:24:00+00:00               False  1600194361806954497   
880  2022-08-20 13:41:48+00:00               False  1560985454152978435   
637  2023-01-10 19:08:53+00:00               False  1612889232657289216   
189  2022-11-05 17:08:07+00:00               False  1588941242473267203   

                                                                                                                                                      text  \
353                           Mujer denuncia que es amenazada por su expareja en Comas: “No hay día que yo no tenga miedo” | VIDEO https://t.co/WzrF97ePYe   
183   #ALVUELO | Antauro Humala propuso cerrar el Congreso si se aprueba ley que impide postular a los sentenciados por homicidio. https://t.co/39BU2FjYK2   
324                                                    Irán amenaza a famosos y medios por protestas tras la muerte de Mahsa Amini https://t.co/v3BDtVkdvb   
92                                          Elecciones 2022: candidatos a la Alcaldía de Lima debaten este domingo a las 9:00 p.m. https://t.co/1xbLvtdQL9   
683                                                            Comer para vivir: ¿Por qué algunos no recomiendan la leche de vaca? https://t.co/5R4CccGG56   
655                                 Voto de confianza: Alianza para el Progreso propone postergar presentación de gabinete Otárola https://t.co/4m9GLSqEDS   
1143                                                 Qatar 2022: Samuel Eto’o golpea a youtuber a la salida de estadio mundialista https://t.co/dxUzfxLWgi   
880                              Miraflores: detienen a delincuente que robó joyería y se llevó artículos valorizados en S/ 80 mil https://t.co/jygyHX78DX   
637                                                                                    Gabinete Otárola solicita voto de confianza https://t.co/nfx9vcTb3w   
189               Policía sobre marcha nacional contra Pedro Castillo: protesta debe ser pacífica, sin armas y no afectar derechos https://t.co/FYF4yN3zB5   

      retweet_count  reply_count  like_count  quote_count referenced_tweets  \
353               2            0           3            0               NaN   
183               1            2           5            0               NaN   
324               0            0          17            0               NaN   
92                1            0           3            1               NaN   
683               0            0           0            0               NaN   
655               0            1           0            0               NaN   
1143              1            0           1            0               NaN   
880               0            0           6            0               NaN   
637               1            3           6            0               NaN   
189               0            1           1            1               NaN   

            newspaper edit_history_tweet_ids  impression_count hour_posted  \
353      diariocorreo  [1612876136089899009]          1,170.00    18:16:51   
183         elbuho_pe  [1574605695340597248]               NaN    03:43:47   
324   elcomercio_peru  [1575621121596182531]               NaN    22:58:43   
92            tromepe                    NaN               NaN    14:54:13   
683         diarioojo  [1600221298151591976]               NaN    20:11:02   
655    peru21noticias  [1612865534684532760]            995.00    17:34:43   
1143   peru21noticias  [160019436180695

## Text cleaning and tokenization

When it comes to text processing, and specially for tweets, there are some common text patterns that do not add any meaning to the message being conveyed. For example: links, hashtags and mentions.

In [20]:
def number_processing(text: str) -> str:
    """Takes a string, finds numbers on it, converts numbers to words and returns string with numbers replaced

    Args:
        text (str): text string to be processed

    Returns:
        str: string with numbers processed
    """
    numbers = re.findall(r"\b\d+\b", text)

    if numbers is []:
        return text

    for number in numbers:
        word_number = num2words(float(number), lang="es")
        text = re.sub(number, word_number, text)

    return text

In [21]:
def clean_text_first_pass(text):
    """Get rid of other punctuation and non-sensical text identified.

    Args:
        text (string): text to be processed.
    """
    text = text.lower()
    text = re.sub("http[s]?(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+", "", text) # Eliminates URLs
    text = re.sub("[%s]" % re.escape(string.punctuation), "", text) # Eliminates punctuarion
    text = re.sub("[‘’“”…«»►¿¡|│`]", "", text)
    text = re.sub("\n", " ", text)

    return text

first_pass = lambda x: clean_text_first_pass(x)

In [22]:
data["text_clean"] = data["text"].apply(number_processing)
data["text_clean"] = data["text_clean"].apply(first_pass)
data["text_clean"]

0                                                                                                                                                     venezuela y colombia retoman relaciones diplomáticas rotas hace tres años 
2                                                                                                                                                         amlo afirma que familias ya aceptaron plan de rescate de diez mineros 
3                                                                                                                                                   zelensky los ocupantes rusos sentirán las consecuencias de futuras acciones 
5                                                                                                                                                   autoridades confirman transmisión comunitaria de viruela del mono en panamá 
7                                                                                                   

In [23]:
data[data["possibly_sensitive"] == True]

created_at  possibly_sensitive                   id  \
108 2022-10-02 03:09:17+00:00                True  1576408955529707521   
742 2022-12-05 21:35:28+00:00                True  1599880158810365977   
249 2022-11-04 17:16:09+00:00                True  1588580874186104832   

                                                                                                                                                 text  \
108                                                           Bebé recién nacido fue encontrado en la basura al sur de Bogotá https://t.co/WJCnELvkR0   
742                              Aumentan a 40 las niñas entre 11 a 14 años que ya se convirtieron en madres en la región Ica https://t.co/cP9HBb7Bkd   
249  Vasectomía gratis del 14 al 18 de noviembre en Lima: ¿afecta el deseo sexual? todo sobre este procedimiento para varones https://t.co/DQ9x0n7HBe   

     retweet_count  reply_count  like_count  quote_count referenced_tweets  \
108              4            1          12            0               NaN   
742              1            5           4            0               NaN   
249              1            0           2            0               NaN   

           newspaper edit_history_tweet_ids  impression_count hour_posted  \
108  elcomercio_peru  [1576408955529707521]               NaN    03:09:17   
742     diariocorreo  [1599880158810365977]               NaN    21:35:28   
249        diarioojo  [1588580874186104832]               NaN    17:16:09   

    mentions hasthags  \
108       []       []   
742       []       []   
249       []       []   

                                                                                                                             text_clean  
108                                                                    bebé recién nacido fue encontrado en la basura al sur de bogotá   
742                          aumentan a cuarenta las niñas entre once a catorce años que ya se convirtieron en madres en la región ica   
249  vasectomía gratis del catorce al dieciocho de noviembre en lima afecta el deseo sexual todo sobre este procedimiento para varones

In [24]:
data.head()

created_at  possibly_sensitive                   id  \
0 2022-08-28 23:57:24+00:00               False  1564039479391838209   
2 2022-08-28 23:29:00+00:00               False  1564032331706470401   
3 2022-08-28 23:14:11+00:00               False  1564028601053347843   
5 2022-08-28 22:54:58+00:00               False  1564023766937731073   
7 2022-08-28 22:30:25+00:00               False  1564017585561141248   

                                                                                                                          text  \
0                            Venezuela y Colombia retoman relaciones diplomáticas rotas hace tres años https://t.co/L6uVA6LcEE   
2                                  AMLO afirma que familias ya aceptaron plan de rescate de 10 mineros https://t.co/dG3VJXWgNa   
3                       Zelensky: los ocupantes rusos sentirán las consecuencias de “futuras acciones” https://t.co/mNJTLz0SS7   
5                          Autoridades confirman transmisión comunitaria de viruela del mono en Panamá https://t.co/EBFcdrHz4Y   
7  Las imágenes de los enfrentamientos entre seguidores de Cristina Kirchner y la policía en Argentina https://t.co/BYalmVyPBF   

   retweet_count  reply_count  like_count  quote_count referenced_tweets  \
0              0            0           6            1               NaN   
2              0            0           2            0               NaN   
3              6            7          18            1               NaN   
5              1            0           1            1               NaN   
7              3            0           8            0               NaN   

         newspaper edit_history_tweet_ids  impression_count hour_posted  \
0  elcomercio_peru                    NaN               NaN    23:57:24   
2  elcomercio_peru                    NaN               NaN    23:29:00   
3  elcomercio_peru                    NaN               NaN    23:14:11   
5  elcomercio_peru                    NaN               NaN    22:54:58   
7  elcomercio_peru                    NaN               NaN    22:30:25   

  mentions hasthags  \
0       []       []   
2       []       []   
3       []       []   
5       []       []   
7       []       []   

                                                                                             text_clean  
0                            venezuela y colombia retoman relaciones diplomáticas rotas hace tres años   
2                                amlo afirma que familias ya aceptaron plan de rescate de diez mineros   
3                          zelensky los ocupantes rusos sentirán las consecuencias de futuras acciones   
5                          autoridades confirman transmisión comunitaria de viruela del mono en panamá   
7  las imágenes de los enfrentamientos entre seguidores de cristina kirchner y la policía en argentina

From checking the resulting text I found that there are some tweets that contain emojis that haven't been removed. For that I will use the `emoji` package.

In [25]:
replace_emojis = lambda x: emoji.replace_emoji(x, "")

In [26]:
data["text_clean"] = data["text_clean"].apply(replace_emojis)
data.sample(10)

created_at  possibly_sensitive                   id  \
347  2022-09-29 20:09:18+00:00               False  1575578483731808256   
1386 2022-08-17 22:31:52+00:00               False  1560031683990142981   
839  2022-11-02 20:01:01+00:00               False  1587897590116679680   
623  2022-11-01 23:30:50+00:00               False  1587588003056472065   
749  2022-08-24 15:55:28+00:00               False  1562468641781587970   
2405 2022-08-15 00:43:02+00:00               False  1558977530937360388   
262  2023-01-13 13:38:02+00:00               False  1613893134156529665   
166  2022-09-29 22:07:38+00:00               False  1575608264909365248   
299  2022-09-27 20:51:44+00:00               False  1574864389362032651   
722  2023-01-11 16:33:10+00:00               False  1613212430653616130   

                                                                                                                                                                                                                                      text  \
347                                                                                                                                     Vladimir Putin ordena enviar a sus casas a los rusos movilizados por error https://t.co/TzUfmqU4gA   
1386                                                                                                                                La delincuencia jaquea a peruanos: aumenta número de víctimas a nivel nacional https://t.co/gwQABENmHR   
839                                                                                                                              ¿Qué es ‘El Tren de Aragua’? La banda que extorsiona y amenaza a ‘Cuto’ Guadalupe https://t.co/7WkiZPsdNN   
623                                                                                                          Valery Revello se luce con Ale Venturo en fiesta de la hija de Melissa Paredes y Rodrigo Cuba | VIDEO https://t.co/nSVs2cuBcg   
749                                                                                                “Al fondo hay sitio”: ‘Alessia’ destruirá a ‘Jaimito’ haciendo que pase la vergüenza de su vida con cruel broma https://t.co/6px2BYkKmC   
2405                                                                                          RT @rajesdeloficio: La fujimorista Milagros Takayama es la nueva jefa del Fondo Editorial del Congreso de la República sin cumplir con el p…   
262                                                                                                                                        Gobierno agiliza nuevos subsidios a familias para reactivar su economía https://t.co/DjatyLrwpD   
166                                                                         Estampas nocturnas: comentario al cortometraje de Hong Kong 'La Noche' https://t.co/mtvBiyjv3k\n\nPor: ✍ Ernesto Carlín @tanquedecasma https://t.co/7WzsGvZBuG   
299   ⬆ El Ministerio de Comercio Exterior y Turismo (@MINCETUR) proyecta más de US$ 2,530 millones en ingresos por turismo interno en 2022, en el marco del Día Mundial del Turismo.\n\n👉 https://t.co/p1iAVYAzjz https://t.co/94HLLITF6s   
722                                                                                                                                                   Los diez “proyectos emblemáticos” en la agenda del Otárola\n https://t.co/EpONVgxKk6   

      retweet_count  reply_count  like_count  quote_count  \
347               0            1          17            0   
1386              1            0           1            0   
839               2            1           2            0   
623               0            0           2            0   
749               0            0           2            0   
2405            939            0           0            0   
262               1            3           2            0   
166               2            0          32            0   
299               0       

Also, form redoing the analysis, and looking at the tweeter feeds from many of the newspapers I found that there are some patterns of writing that do not add to the content, like calls to action, that interact with the audience, but do not add any significance to the headline. I'll be checking at the twitter feed for such patterns and add them during cleaning. I'm not adding them as stopwords because these calls to action in specific are groups of words.

In [27]:
def clean_text_second_pass(text):
    """Get rid of other punctuation and non-sensical text identified.

    Args:
        text (string): text to be processed.
    """
    text = re.sub("click aquí", "", text)
    text = re.sub("opinión", "", text)
    text = re.sub("rt ", "", text)
    text = re.sub('lee aquí el blog de', '', text)
    text = re.sub('vía gestionpe', '', text)
    text = re.sub('entrevista exclusiva', '', text)
    text = re.sub('en vivo', '', text)
    text = re.sub('entérate más aquí', '', text)
    text = re.sub('lee la columna de', '', text)
    text = re.sub('lee y comenta', '', text)
    text = re.sub('lea hoy la columna de', '', text)
    text = re.sub('escrito por', '', text)
    text = re.sub('lee la nota aquí', '', text)
    text = re.sub('una nota de', '', text)
    text = re.sub('aquí la nota', '', text)
    text = re.sub('nota completa aquí', '', text)
    text = re.sub('nota completa', '', text)
    text = re.sub('lee más', '', text)
    text = re.sub('lee aquí', '', text)

    text = re.sub("  ", " ", text)
    text = re.sub(" \w ", " ", text)
    text = re.sub("^(plusg)", "", text)
    text = re.sub("( video )$", "", text)
    text = re.sub("( lee )$", "", text)
    text = re.sub("( lee la )$", "", text)

    return text

second_pass = lambda x: clean_text_second_pass(x)

In [29]:
data["text_clean"] = data.text_clean.apply(second_pass)

created_at  possibly_sensitive                   id  \
122  2022-11-04 14:43:38+00:00               False  1588542491665784832   
1053 2022-08-22 23:05:19+00:00               False  1561852043425419266   
295  2023-01-12 12:55:37+00:00               False  1613520073250963457   
1466 2022-09-26 19:57:09+00:00               False  1574488264727314453   
1105 2022-08-22 18:31:29+00:00               False  1561783131514044418   
144  2022-08-25 22:50:13+00:00               False  1562935407322337281   
412  2022-11-04 18:54:34+00:00               False  1588605642796851202   
734  2022-09-29 00:50:14+00:00               False  1575286795641708544   
340  2022-09-30 00:16:08+00:00               False  1575640604679323650   
1061 2022-09-28 09:00:02+00:00               False  1575047672163143682   

                                                                                                                                                                                                                                                                                               text  \
122   💰 El @MidisPeru alcanzó una ejecución presupuestal de 80.3 % por el cumplimiento de metas de sus programas sociales, así como por el presupuesto destinado en alimentación a población vulnerable, ollas comunes y comedores populares. \n\n👉 https://t.co/bAtkOB30FI https://t.co/6eaT1QPRfj   
1053                                                                                                                                                 RT @LR_Deportes: ⚠️📺 #VIDEO | ¡No le gustó nada! Benavente fue captado en concierto y se molestó con el reportero\n\nEl ‘Chaval’ se fue de fi…   
295                                                                                                                                                       Hugo García grita de emoción al ver a Alessia participando en ronda preliminar del Miss Universo: “Vamos mi amor” https://t.co/fjljmLYHtT   
1466                                                                                                                                                                                   ‘Precio de la guerra’ en Ucrania lastrará la economía mundial en 2023, según la OCDE https://t.co/nOgy6yy7yk   
1105                                                                                                                                                                  Congresistas exigen respuestas por liberación de Antauro Humala y las noticias del día en #LRNoticias https://t.co/9gpW6b4UHj   
144            El presidente de la República, Pedro Castillo Terrones, señaló este jueves que el desarrollo del país se debe construir entre todos los peruanos sin distinción y no solamente esperar al gobierno y a las autoridades nacionales. 👉 https://t.co/5tDZ9lu6mX https://t.co/ZxnGEuDpct   
412                                                                                                                                                                        Tercer Simulacro Nacional Multipeligro: cuándo se realizará, a qué hora y cómo puedes participar https://t.co/uu4Ew2UXaF   
734                                                                                                                                                                                                                ¿Quiénes son los candidatos a la alcaldía de Miraflores? https://t.co/cpTKvq1o4r   
340                                                                                                                                                                   Roberto Sánchez sobre Gonzalo Alegría: Juntos por el Perú “tiene sus propios mecanismos y dirigentes” https://t.co/ZDfPj9HOKd   
1061                                                                                                                                                                             "Indomable, Colosso Wines", lee aquí el #blog de José Bracamonte ► 

In [30]:
data.reset_index().to_feather(f"{BASE_DIR}/data/interim/data_clean-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.feather")

## Organizing the data

Now I need to get the data in both of the standar text formats:

1. **Corpus -** a collection of text
2. **Document-Term matrix -** word counts in matrix format

In the case of the tweets, I will start by combining all the clean texts and in the case of *Document-term matrix* tokenising the result.

In [32]:
df_clean = pd.read_feather(f"{BASE_DIR}/data/interim/data_clean-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.feather")
df_clean.set_index("index", inplace=True)

In [34]:
df_clean.sample(5)

created_at  possibly_sensitive                   id  \
index                                                                      
590   2022-09-28 11:47:37+00:00               False  1575089844405116929   
1257  2022-08-18 14:08:30+00:00               False  1560267397335961601   
581   2022-08-23 17:34:08+00:00               False  1562131086116880385   
359   2023-01-13 13:25:11+00:00               False  1613889901702914048   
1422  2022-08-20 15:45:49+00:00               False  1561016662891151361   

                                                                                                                                                                                                                                                                                            text  \
index                                                                                                                                                                                                                                                                                              
590                                                                                                                                                                                    Magaly le da con palo a la mamá de María Fe: “La suegra feliz con los viajes” \n\nhttps://t.co/rfMI1c74ia   
1257                                                                                                                                                                                                              Tumbes: Dos candidatos de Fuerza Popular son excluidos https://t.co/ieraPI9nTL   
581                                                                                                                                                                                      ¿Cuánto será el pago del Bono Alimentario para los beneficiarios de Pensión 65? https://t.co/BHX7qUnYzr   
359    #CuatroD | Mientras la cifra de fallecidos a raíz de las protestas sigue en aumento, el premier Otárola descartó que la presidenta Dina Boluarte vaya a renunciar. Analizamos el tema con @Techtulia, @alvarezrodrich y @lauermirko.\n\n📺 Míralo #ENVIVO, aquí ↓\nhttps://t.co/byZyCUVWGw   
1422                                                                                                                                                             Viruela del mono en Perú: estas son las razones que explicarían el incremento considerable de contagios https://t.co/ZgqpoLrlaA   

       retweet_count  reply_count  like_count  quote_count referenced_tweets  \
index                                                                          
590                0            0           2            0              None   
1257               0            0           2            0              None   
581                0            0           2            0              None   
359                7           19          16            1              None   
1422               0            0           0            0              None   

             newspaper edit_history_tweet_ids  impression_count hour_posted  \
index                                                                         
590          diarioojo  [1575089844405116929]               NaN    11:47:37   
1257      diariocorreo                   None               NaN    14:08:30   
581    elcomercio_peru                   None               NaN    17:34:08   
359     larepublica_pe  [1613889901702914048]          5,148.00    13:25:11   
1422           tromepe                   None               NaN    15:45:49   

                                      mentions           hasthags  \
index                                                               
590                                         []                 []   
1257                                        []                 []   
581                                         []      

In [35]:
stats_data = df_clean.drop(["text", "text_clean"], axis=1)

In [36]:
stats_data.head()

created_at  possibly_sensitive                   id  \
index                                                                      
0     2022-08-28 23:57:24+00:00               False  1564039479391838209   
2     2022-08-28 23:29:00+00:00               False  1564032331706470401   
3     2022-08-28 23:14:11+00:00               False  1564028601053347843   
5     2022-08-28 22:54:58+00:00               False  1564023766937731073   
7     2022-08-28 22:30:25+00:00               False  1564017585561141248   

       retweet_count  reply_count  like_count  quote_count referenced_tweets  \
index                                                                          
0                  0            0           6            1              None   
2                  0            0           2            0              None   
3                  6            7          18            1              None   
5                  1            0           1            1              None   
7                  3            0           8            0              None   

             newspaper edit_history_tweet_ids  impression_count hour_posted  \
index                                                                         
0      elcomercio_peru                   None               NaN    23:57:24   
2      elcomercio_peru                   None               NaN    23:29:00   
3      elcomercio_peru                   None               NaN    23:14:11   
5      elcomercio_peru                   None               NaN    22:54:58   
7      elcomercio_peru                   None               NaN    22:30:25   

      mentions hasthags  
index                    
0           []       []  
2           []       []  
3           []       []  
5           []       []  
7           []       []

In [41]:
stats_data.reset_index().to_feather(f"{BASE_DIR}/data/processed/stats_data-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.feather")

### Corpus

The corpus corresponds to the data clean from the step above.

In [35]:
df_corpus = df_clean[["id", "text", "created_at", "newspaper", "text_clean"]].reset_index()
df_corpus.rename(columns={"text_clean": "corpus"}, inplace=True)

In [36]:
df_corpus.to_feather(f"{BASE_DIR}/data/processed/corpus-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.feather")

### Document-Term Matrix

From the corpus constructed in the step above I'll proceed to tokenizethe text to use with further techniques. For that I'll use scikit-learn's `CountVectorizer`, where every row represents a document and each column is a different row.

I'll also remove stop words.

In [5]:
nlp = spacy.load('es_core_news_sm')

In [6]:
data_dtm = pd.read_feather(f"{BASE_DIR}/data/processed/corpus-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.feather")

In [7]:
data_dtm.drop(["index"], axis=1, inplace=True)

In [9]:
data_dtm.sample(5)

id  \
32370  1599831323199389700   
3350   1562442570529091589   
17382  1601091651576991744   
33143  1559305536356732931   
2134   1600834997736607745   

                                                                                                                                                                                                                                                              text  \
32370                                                                                                                   Gobierno tomará acciones legales en caso de que se concrete la vacancia contra Pedro Castillo, anuncia Félix Chero https://t.co/XGEYvsq5cQ   
3350   ⚠️ Dictan 18 meses de prisión preventiva a trabajadora bancaria que transfirió S/ 110.000 a su cuenta\n\nLa mujer fue detenida el último 15 de agosto en flagrancia. La investigada realizó 7 transferencias a su cuenta personal.\nhttps://t.co/829JoJJbZF   
17382                                                                                                                                                      Betssy Chávez: conoce las conversaciones que la conectan con el golpe de Estado https://t.co/6LKhfp5dWj   
33143                                                              El titular de @pcmperu, Aníbal Torres, participó esta tarde en el segundo Simulacro Nacional Multipeligro, en la sede de Palacio de Gobierno. 👉 https://t.co/xEFAkguYlo https://t.co/IiBlluWHNE   
2134                                #Editorial | "Es cierto que el golpe que dio Castillo no prosperó, pero ello –contrariamente a lo que algunos de sus todavía simpatizantes se aventuraban a asegurar ayer– no lo hace menos golpe".\n\nhttps://t.co/rRU8KBCvso   

                     created_at        newspaper  \
32370 2022-12-05 18:21:25+00:00        diarioojo   
3350  2022-08-24 14:11:52+00:00   larepublica_pe   
17382 2022-12-09 05:49:31+00:00          tromepe   
33143 2022-08-15 22:26:25+00:00  DiarioElPeruano   
2134  2022-12-08 12:49:40+00:00  elcomercio_peru   

                                                                                                                                                                                                                                           corpus  
32370                                                                                                                          gobierno tomará acciones legales en caso de que se concrete la vacancia contra pedro castillo anuncia félix chero   
3350    dictan dieciocho meses de prisión preventiva trabajadora bancaria que transfirió ciento diezcero su cuenta la mujer fue detenida el último quince de agosto en flagrancia la investigada realizó siete transferencias su cuenta personal   
17382                                                                                                                                                             betssy chávez conoce las conversaciones que la conectan con el golpe de estado   
33143                                                                                                   el titular de pcmperu aníbal torres participó esta tarde en el segundo simulacro nacional multipeligro en la sede de palacio de gobierno   
2134                                                    editorial es cierto que el golpe que dio castillo no prosperó pero ello –contrariamente lo que algunos de sus todavía simpatizantes se aventuraban asegurar ayer– no lo hace menos golpe

In [10]:
data_dtm.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 34924 entries, 0 to 34923
Data columns (total 5 columns):
 #   Column      Non-Null Count  Dtype              
---  ------      --------------  -----              
 0   id          34924 non-null  object             
 1   text        34924 non-null  object             
 2   created_at  34924 non-null  datetime64[ns, UTC]
 3   newspaper   34924 non-null  object             
 4   corpus      34924 non-null  object             
dtypes: datetime64[ns, UTC](1), object(4)
memory usage: 1.3+ MB


In [11]:
data_dtm["doc"] = data_dtm["corpus"].apply(lambda x: nlp(x))
data_dtm["doc"]

0                                                                                                                                                                           (venezuela, colombia, retoman, relaciones, diplomáticas, rotas, hace, tres, años)
1                                                                                                                                                                          (amlo, afirma, que, familias, ya, aceptaron, plan, de, rescate, de, diez, mineros)
2                                                                                                                                                                      (zelensky, los, ocupantes, rusos, sentirán, las, consecuencias, de, futuras, acciones)
3                                                                                                                                                                      (autoridades, confirman, transmisión, comunitaria, de, viruela, del, mo

In [12]:
data_dtm["token"] = data_dtm["doc"].apply(lambda doc: [t.orth_ for t in doc if not t.is_punct | t.is_stop | t.is_space])
data_dtm["lemma"] = data_dtm["doc"].apply(lambda doc: [t.lemma_ for t in doc if not t.is_punct | t.is_stop | t.is_space])

In [13]:
data_dtm = data_dtm.loc[data_dtm["corpus"] != ""]
data_dtm = data_dtm.loc[data_dtm["token"].map(lambda d: len(d)) > 0]

In [14]:
data_dtm.head()

id  \
0  1564039479391838209   
1  1564032331706470401   
2  1564028601053347843   
3  1564023766937731073   
4  1564017585561141248   

                                                                                                                          text  \
0                            Venezuela y Colombia retoman relaciones diplomáticas rotas hace tres años https://t.co/L6uVA6LcEE   
1                                  AMLO afirma que familias ya aceptaron plan de rescate de 10 mineros https://t.co/dG3VJXWgNa   
2                       Zelensky: los ocupantes rusos sentirán las consecuencias de “futuras acciones” https://t.co/mNJTLz0SS7   
3                          Autoridades confirman transmisión comunitaria de viruela del mono en Panamá https://t.co/EBFcdrHz4Y   
4  Las imágenes de los enfrentamientos entre seguidores de Cristina Kirchner y la policía en Argentina https://t.co/BYalmVyPBF   

                 created_at        newspaper  \
0 2022-08-28 23:57:24+00:00  elcomercio_peru   
1 2022-08-28 23:29:00+00:00  elcomercio_peru   
2 2022-08-28 23:14:11+00:00  elcomercio_peru   
3 2022-08-28 22:54:58+00:00  elcomercio_peru   
4 2022-08-28 22:30:25+00:00  elcomercio_peru   

                                                                                               corpus  \
0                            venezuela colombia retoman relaciones diplomáticas rotas hace tres años    
1                              amlo afirma que familias ya aceptaron plan de rescate de diez mineros    
2                        zelensky los ocupantes rusos sentirán las consecuencias de futuras acciones    
3                        autoridades confirman transmisión comunitaria de viruela del mono en panamá    
4  las imágenes de los enfrentamientos entre seguidores de cristina kirchner la policía en argentina    

                                                                                                                doc  \
0                                 (venezuela, colombia, retoman, relaciones, diplomáticas, rotas, hace, tres, años)   
1                                (amlo, afirma, que, familias, ya, aceptaron, plan, de, rescate, de, diez, mineros)   
2                            (zelensky, los, ocupantes, rusos, sentirán, las, consecuencias, de, futuras, acciones)   
3                            (autoridades, confirman, transmisión, comunitaria, de, viruela, del, mono, en, panamá)   
4  (las, imágenes, de, los, enfrentamientos, entre, seguidores, de, cristina, kirchner, la, policía, en, argentina)   

                                                                             token  \
0            [venezuela, colombia, retoman, relaciones, diplomáticas, rotas, años]   
1                      [amlo, afirma, familias, aceptaron, plan, rescate, mineros]   
2         [zelensky, ocupantes, rusos, sentirán, consecuencias, futuras, acciones]   
3        [autoridades, confirman, transmisión, comunitaria, viruela, mono, panamá]   
4  [imágenes, enfrentamientos, seguidores, cristina, kirchner, policía, argentina]   

                                                                        lemma  
0            [venezuela, colombia, retomar, relación, diplomático, roto, año]  
1                    [amlo, afirmar, familia, aceptar, plan, rescate, minero]  
2            [zelensky, ocupante, ruso, sentir, consecuencia, futuro, acción]  
3     [autoridad, confirmar, transmisión, comunitario, viruela, mono, panamá]  
4  [imagen, enfrentamiento, seguidor, cristina, kirchner, policía, argentina]

In [15]:
print(data_dtm.head().to_markdown())

|    |                  id | text                                                                                                                        | created_at                | newspaper       | corpus                                                                                            | doc                                                                                               | token                                                                                         | lemma                                                                                    |
|---:|--------------------:|:----------------------------------------------------------------------------------------------------------------------------|:--------------------------|:----------------|:--------------------------------------------------------------------------------------------------|:--------------------------------------------------------------------------------------------------|:-----------

In [25]:
data_dtm.to_pickle(f"{BASE_DIR}/data/processed/data-dtm-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.pkl")

In [26]:
dtm = pd.DataFrame(data_dtm[["id", "lemma"]].explode("lemma").groupby(by="id").value_counts())
dtm.rename({0: "count"}, axis=1, inplace=True)
dtm = dtm.reset_index()

In [27]:
dtm = dtm.pivot(index="id", columns="lemma", values="count")

In [28]:
dtm.fillna(0.00, inplace=True)

In [29]:
dtm.head()

lemma                 aa  aaaaatención  aaaatención  aactor  aafp  aaguinagar  \
id                                                                              
1558966707611385861 0.00          0.00         0.00    0.00  0.00        0.00   
1558966968039997441 0.00          0.00         0.00    0.00  0.00        0.00   
1558967193043361792 0.00          0.00         0.00    0.00  0.00        0.00   
1558967616777109510 0.00          0.00         0.00    0.00  0.00        0.00   
1558968396674473985 0.00          0.00         0.00    0.00  0.00        0.00   

lemma                aahh  aap  aar  abad  ...  𝗨́𝗻𝗲𝘁𝗲  𝗩𝗮𝗹𝗹𝗲   𝗱𝗲  𝗱𝗲𝗹  \
id                                         ...                            
1558966707611385861  0.00 0.00 0.00  0.00  ...    0.00   0.00 0.00 0.00   
1558966968039997441  0.00 0.00 0.00  0.00  ...    0.00   0.00 0.00 0.00   
1558967193043361792  0.00 0.00 0.00  0.00  ...    0.00   0.00 0.00 0.00   
1558967616777109510  0.00 0.00 0.00  0.00  ...    0.00   0.00 0.00 0.00   
1558968396674473985  0.00 0.00 0.00  0.00  ...    0.00   0.00 0.00 0.00   

lemma                𝗲𝗱𝗶𝘁𝗼𝗿𝗶𝗮𝗹  𝗵𝗿𝘀   𝗹𝗮  𝗻𝗼𝘃𝗶𝗲𝗺𝗯𝗿𝗲  𝗽𝗿𝗲𝘀𝗲𝗻𝘁𝗮𝗰𝗶𝗼́𝗻  󠁧󠁢󠁥󠁮󠁧󠁿  
id                                                                          
1558966707611385861       0.00 0.00 0.00       0.00           0.00    0.00  
1558966968039997441       0.00 0.00 0.00       0.00           0.00    0.00  
1558967193043361792       0.00 0.00 0.00       0.00           0.00    0.00  
1558967616777109510       0.00 0.00 0.00       0.00           0.00    0.00  
1558968396674473985       0.00 0.00 0.00       0.00           0.00    0.00  

[5 rows x 24473 columns]

In [30]:
dtm.info()

<class 'pandas.core.frame.DataFrame'>
Index: 34851 entries, 1558966707611385861 to 1614774185221308416
Columns: 24473 entries, aa to 󠁧󠁢󠁥󠁮󠁧󠁿
dtypes: float64(24473)
memory usage: 6.4+ GB


In [31]:
dtm.reset_index().to_feather(f"{BASE_DIR}/data/processed/dtm-{TIME_STAMPS[0]}-{TIME_STAMPS[-1]}.feather")